In [1]:
# import modules
import requests
import pandas as pd

# create request header
headers = {'User-Agent': "edwarddramirez@hotmail.com"}

# get all companies data
companyTickers = requests.get(
    "https://www.sec.gov/files/company_tickers.json",
    headers=headers
    )

# review response / keys
print(companyTickers.json().keys())

# format response to dictionary and get first key/value
firstEntry = companyTickers.json()['0']

# parse CIK // without leading zeros
directCik = companyTickers.json()['0']['cik_str']

# dictionary to dataframe
companyData = pd.DataFrame.from_dict(companyTickers.json(),
                                     orient='index')

# add leading zeros to CIK
companyData['cik_str'] = companyData['cik_str'].astype(
                           str).str.zfill(10)

# review data
print(companyData[:1])

/home/edr/mambaforge/envs/cbase/lib/python3.9/site-packages/pandas/core/computation/expressions.py:21: UserWarning: Pandas requires version '2.8.4' or newer of 'numexpr' (version '2.7.3' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
/home/edr/mambaforge/envs/cbase/lib/python3.9/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.2' currently installed).
  from pandas.core import (


dict_keys(['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '21', '22', '23', '24', '25', '26', '27', '28', '29', '30', '31', '32', '33', '34', '35', '36', '37', '38', '39', '40', '41', '42', '43', '44', '45', '46', '47', '48', '49', '50', '51', '52', '53', '54', '55', '56', '57', '58', '59', '60', '61', '62', '63', '64', '65', '66', '67', '68', '69', '70', '71', '72', '73', '74', '75', '76', '77', '78', '79', '80', '81', '82', '83', '84', '85', '86', '87', '88', '89', '90', '91', '92', '93', '94', '95', '96', '97', '98', '99', '100', '101', '102', '103', '104', '105', '106', '107', '108', '109', '110', '111', '112', '113', '114', '115', '116', '117', '118', '119', '120', '121', '122', '123', '124', '125', '126', '127', '128', '129', '130', '131', '132', '133', '134', '135', '136', '137', '138', '139', '140', '141', '142', '143', '144', '145', '146', '147', '148', '149', '150', '151', '152', '153', '154', '155', '156', 

In [2]:
companyData

cik_str ticker                                   title
0      0000789019   MSFT                          MICROSOFT CORP
1      0000320193   AAPL                              Apple Inc.
2      0001045810   NVDA                             NVIDIA CORP
3      0001018724   AMZN                          AMAZON COM INC
4      0001652044  GOOGL                           Alphabet Inc.
...           ...    ...                                     ...
10426  0001901336  ALCYW  Alchemy Investments Acquisition Corp 1
10427  0001901336  ALCYU  Alchemy Investments Acquisition Corp 1
10428  0001977303  ARLTF                    Arcadium Lithium plc
10429  0001974044  MNYWW                           MoneyHero Ltd
10430  0001998781  IBACU                    IB Acquisition Corp.

[10431 rows x 3 columns]

In [6]:
df = companyData[['ticker', 'title']].copy()

def get_total_assets(cik):
    # get 10-Q data
    companyFacts = requests.get(
        f'https://data.sec.gov/api/xbrl/companyfacts/CIK{cik}.json',
        headers=headers
        )
    # parse response
    return companyFacts.json()

In [7]:
cik = companyData.cik_str.values[0]
companyFacts = requests.get(
    f'https://data.sec.gov/api/xbrl/companyfacts/CIK{cik}.json',
    headers=headers
    )

In [11]:
get_total_assets(companyData.cik_str.values[0])

{'cik': 789019,
 'entityName': 'MICROSOFT CORPORATION',
 'facts': {'dei': {'EntityCommonStockSharesOutstanding': {'label': 'Entity Common Stock, Shares Outstanding',
    'description': "Indicate number of shares or other units outstanding of each of registrant's classes of capital or common stock or other ownership interests, if and as stated on cover of related periodic report. Where multiple classes or units exist define each class/interest by adding class of stock items such as Common Class A [Member], Common Class B [Member] or Partnership Interest [Member] onto the Instrument [Domain] of the Entity Listings, Instrument.",
    'units': {'shares': [{'end': '2009-10-19',
       'val': 8879121378,
       'accn': '0001193125-09-212454',
       'fy': 2010,
       'fp': 'Q1',
       'form': '10-Q',
       'filed': '2009-10-23',
       'frame': 'CY2009Q3I'},
      {'end': '2010-01-25',
       'val': 8770460922,
       'accn': '0001193125-10-015598',
       'fy': 2010,
       'fp': 'Q2',
 

In [25]:
df['Assets'] = companyData['cik_str'].apply(lambda x: get_total_assets(x))

KeyError: 'us-gaap'

In [3]:
cik = companyData[0:1].cik_str[0]

# get company specific filing metadata
filingMetadata = requests.get(
    f'https://data.sec.gov/submissions/CIK{cik}.json',
    headers=headers
    )

# review json 
print(filingMetadata.json().keys())
filingMetadata.json()['filings']
filingMetadata.json()['filings'].keys()
filingMetadata.json()['filings']['recent']
filingMetadata.json()['filings']['recent'].keys()

# dictionary to dataframe
allForms = pd.DataFrame.from_dict(
             filingMetadata.json()['filings']['recent']
             )

# review columns
allForms.columns
allForms[['accessionNumber', 'reportDate', 'form']].head(50)

# 10-Q metadata
allForms.iloc[11]

# get company facts data
companyFacts = requests.get(
    f'https://data.sec.gov/api/xbrl/companyfacts/CIK{cik}.json',
    headers=headers
    )

/tmp/ipykernel_27757/229031373.py:1: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cik = companyData[0:1].cik_str[0]


dict_keys(['cik', 'entityType', 'sic', 'sicDescription', 'insiderTransactionForOwnerExists', 'insiderTransactionForIssuerExists', 'name', 'tickers', 'exchanges', 'ein', 'description', 'website', 'investorWebsite', 'category', 'fiscalYearEnd', 'stateOfIncorporation', 'stateOfIncorporationDescription', 'addresses', 'phone', 'flags', 'formerNames', 'filings'])


In [4]:
#review data
companyFacts.json().keys()
companyFacts.json()['facts']
companyFacts.json()['facts'].keys()

dict_keys(['dei', 'us-gaap'])

In [5]:
companyFacts.json()['facts']['us-gaap']['Assets']

{'label': 'Assets',
 'description': 'Sum of the carrying amounts as of the balance sheet date of all assets that are recognized. Assets are probable future economic benefits obtained or controlled by an entity as a result of past transactions or events.',
 'units': {'USD': [{'end': '2009-06-30',
    'val': 77888000000,
    'accn': '0001193125-09-212454',
    'fy': 2010,
    'fp': 'Q1',
    'form': '10-Q',
    'filed': '2009-10-23'},
   {'end': '2009-06-30',
    'val': 77888000000,
    'accn': '0001193125-10-015598',
    'fy': 2010,
    'fp': 'Q2',
    'form': '10-Q',
    'filed': '2010-01-28'},
   {'end': '2009-06-30',
    'val': 77888000000,
    'accn': '0001193125-10-090116',
    'fy': 2010,
    'fp': 'Q3',
    'form': '10-Q',
    'filed': '2010-04-22'},
   {'end': '2009-06-30',
    'val': 77888000000,
    'accn': '0001193125-10-171791',
    'fy': 2010,
    'fp': 'FY',
    'form': '10-K',
    'filed': '2010-07-30',
    'frame': 'CY2009Q2I'},
   {'end': '2009-09-30',
    'val': 816120